# **Exploratory Data Analysis Notebook**

In [1]:
import pandas as pd
import numpy as np
from warnings import filterwarnings
from google.cloud import bigquery
from google.oauth2 import service_account
filterwarnings('ignore')

#### Step 1: View Current Data

In [2]:
pd.set_option('display.max_colwidth', 255)
credentials = service_account.Credentials.from_service_account_file(r"C:\Users\Chase\Downloads\used-car-summer-2023-project-b4807c4731d7.json")

bigquery_client = bigquery.Client(credentials=credentials, project='used-car-summer-2023-project')


query = bigquery_client.query('SELECT * FROM `training_data.wrangled_training_data`').result()
clean_listings = query.to_dataframe()
clean_listings

price  year       make       model                           trim   
0        3795  1997      Honda        CR-V                                 \
1       16880  1997  Chevrolet      Malibu                             LS   
2       12000  1997    Porsche     Boxster                         Manual   
3       12495  1997      Buick     Riviera                      Coupe 3.8   
4       16570  1997  Chevrolet      Camaro                     Z/28 Coupe   
...       ...   ...        ...         ...                            ...   
125831  48000  2024       MINI  Countryman         John Cooper Works ALL4   
125832  57988  2024      Acura         MDX         Technology Package SH-   
125833  56990  2024      Acura         MDX         Technology Package SH-   
125834  56990  2024      Acura         MDX         Technology Package SH-   
125835  94199  2024        GMC      Sierra  Denali Crew Cab Standard Bed    

        mileage exterior_color interior_color  num_accidents  num_owners   
0        153629           Blue           Gray              0         6.0  \
1         14506          Green           Gray              0         5.0   
2         90208         Silver            Red              1        10.0   
3        129768          White          Beige              1         7.0   
4         64243          White          White              0         3.0   
...         ...            ...            ...            ...         ...   
125831     1915          Black          Black              0         1.0   
125832        7         Silver          Black              0         0.0   
125833        7           Blue           Gray              0         0.0   
125834        5           Gray          Brown              0         0.0   
125835        7          White           Gray              0         0.0   

       usage_type          city state  
0        Personal     Englewood    CO  
1        Personal  Grand island    NE  
2        Personal    Scottsdale    AZ  
3           Fleet          Mesa    AZ  
4        Personal      Lakewood    CO  
...           ...           ...   ...  
125831   Personal          Mesa    AZ  
125832   Personal       Boulder    CO  
125833   Personal       Boulder    CO  
125834   Personal       Boulder    CO  
125835   Personal      Marietta    GA  

[125836 rows x 13 columns]

### **Phase 2: Histograms for Numeric Features**

In [3]:
import plotly.express as px

fig = px.histogram(clean_listings['price'], nbins=100)
fig.update_layout(xaxis=dict(showgrid=False), yaxis=dict(showgrid=False), title='Price Distribution')

In [4]:
from pandasql import sqldf
listings_by_state = sqldf('SELECT state, COUNT(*) AS num_listings FROM clean_listings GROUP BY state')

fig = px.choropleth(listings_by_state, locations='state', locationmode="USA-states", scope='usa', color='num_listings', color_continuous_scale='greens')

fig.show()

In [5]:
fig = px.histogram(clean_listings['year'], nbins=30)
fig.update_layout(xaxis=dict(showgrid=False), yaxis=dict(showgrid=False), title='Model Year Distribution')

In [6]:
fig = px.histogram(clean_listings['mileage'], nbins=100)
fig.update_layout(xaxis=dict(showgrid=False), yaxis=dict(showgrid=False), title='Mileage Distribution')

### **Phase 3: Correlation Matrix**

In [7]:
matrix = clean_listings[['price', 'year', 'mileage', 'num_accidents', 'num_owners']].corr()
matrix

price      year   mileage  num_accidents  num_owners
price          1.000000  0.016602 -0.017738      -0.007858   -0.007923
year           0.016602  1.000000 -0.737104      -0.175531   -0.512160
mileage       -0.017738 -0.737104  1.000000       0.183377    0.445780
num_accidents -0.007858 -0.175531  0.183377       1.000000    0.129338
num_owners    -0.007923 -0.512160  0.445780       0.129338    1.000000

### **Descriptive Statistics**

In [8]:
pd.set_option('display.float_format', lambda x: '%.2f' % x)
clean_listings['year'] = clean_listings['year'].astype(int)
clean_listings.describe()

price      year   mileage  num_accidents  num_owners
count    125836.00 125836.00 125836.00      125836.00   125835.00
mean      28175.41   2018.07  56251.71           0.33        1.65
std      315229.30      3.49  38621.85           0.63        0.92
min        1500.00   1997.00      5.00           0.00        0.00
25%       18998.00   2016.00  28134.00           0.00        1.00
50%       24998.00   2019.00  48679.50           0.00        1.00
75%       32995.00   2021.00  78004.00           1.00        2.00
max   111749900.00   2024.00 412031.00           7.00       13.00

### **Bar Charts for Categorical Features**

In [9]:
from pandasql import sqldf
listings_by_make = sqldf("SELECT make, COUNT(*) num_listings FROM clean_listings GROUP BY make")

fig = px.bar(listings_by_make, listings_by_make['make'], listings_by_make['num_listings'], text_auto=True, title="Listings by Make", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [10]:
listings_by_model = sqldf("SELECT make || ' ' || model AS model, COUNT(*) num_listings FROM clean_listings GROUP BY model HAVING num_listings < 50 ORDER BY num_listings DESC")

import plotly.graph_objects as go
import pandas as pd


fig = go.Figure(data=[go.Table(
    header=dict(values=list(listings_by_model.columns),
                fill_color='paleturquoise',
                align='left'),
    cells=dict(values=[listings_by_model.model, listings_by_model.num_listings],
               fill_color='lavender',
               align='left'))
])

fig.show()

##### **Models to Be Concerned About:** Buick Envision, Mitsubishi Eclipse Cross, Hyundai Veloster, FIAT 500, Chevrolet Avanlanche, Nissan Xterra, Nissan Quest

In [11]:
listings_by_ext = sqldf("SELECT exterior_color, COUNT(*) num_listings FROM clean_listings GROUP BY exterior_color")

fig = px.bar(listings_by_ext, listings_by_ext['exterior_color'], listings_by_ext['num_listings'], text_auto=True, title="Listings by Exterior Color", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [12]:
listings_by_int = sqldf("SELECT interior_color, COUNT(*) num_listings FROM clean_listings GROUP BY interior_color")

fig = px.bar(listings_by_int, listings_by_int['interior_color'], listings_by_int['num_listings'], text_auto=True, title="Listings by Interior Color", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [13]:
listings_by_use = sqldf("SELECT usage_type, COUNT(*) num_listings FROM clean_listings GROUP BY usage_type")

fig = px.bar(listings_by_use, listings_by_use['usage_type'], listings_by_use['num_listings'], text_auto=True, title="Listings by Usage Type", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [14]:
listings_by_accidents = sqldf("SELECT num_accidents, COUNT(*) num_listings FROM clean_listings GROUP BY num_accidents")

fig = px.bar(listings_by_accidents, listings_by_accidents['num_accidents'], listings_by_accidents['num_listings'], text_auto=True, title="Listings by # of Accidents", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [15]:
listings_by_owners = sqldf("SELECT num_owners, COUNT(*) num_listings FROM clean_listings GROUP BY num_owners")

fig = px.bar(listings_by_owners, listings_by_owners['num_owners'], listings_by_owners['num_listings'], text_auto=True, title="Listings by # of Owners", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [16]:
clean_listings.to_parquet('wrangled_data.parquet', compression='snappy')

In [17]:
import datetime
if (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 1):
    make = 'chrysler'
    model = 'pacifica'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 2):
    make = 'mitsubishi'
    model = 'mirage'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 3):
    make = 'nissan'
    model = 'altima'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 4):
    make = 'subaru'
    model = 'crosstrek'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 5):
    make = 'acura'
    model = 'mdx'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 6):
    make = 'dodge'
    model = 'grand-caravan'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 7):
    make = 'ram'
    model = '1500'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 8):
    make = 'hyundai'
    model = 'santa-fe'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 9):
    make = 'kia'
    model = 'sorento'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 10):
    make = 'buick'
    model = 'enclave'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 11):
    make = 'audi'
    model = 'q5'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 12):
    make = 'hyundai'
    model = 'kona'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 13):
    make = 'mazda'
    model = 'mx-5-miata'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 14):
    make = 'toyota'
    model = 'avalon'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 15):
    make = 'chevrolet'
    model = 'tahoe'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 16):
    make = 'hyundai'
    model = 'sonata'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 17):
    make = 'volkswagen'
    model = 'golf'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 18):
    make = 'dodge'
    model = 'durango'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 19):
    make = 'lexus'
    model = 'is'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 20):
    make = 'infiniti'
    model = 'q50'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 21):
    make = 'mini'
    model = 'cooper'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 22):
    make = 'lincoln'
    model = 'navigator'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 23):
    make = 'bmw'
    model = '3-series'
elif (datetime.datetime.now().weekday() == 1) & (datetime.datetime.now().hour == 0):
    make = 'mercedes-benz'
    model = 'c-class'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 1):
    make = 'chrysler'
    model = '300'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 2):
    make = 'mitsubishi'
    model = 'outlander'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 3):
    make = 'nissan'
    model = 'sentra'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 4):
    make = 'subaru'
    model = 'outback'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 5):
    make = 'acura'
    model = 'rdx'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 6):
    make = 'mazda'
    model = 'cx-30'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 7):
    make = 'ram'
    model = '2500'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 8):
    make = 'hyundai'
    model = 'tucson'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 9):
    make = 'kia'
    model = 'sportage'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 10):
    make = 'buick'
    model = 'encore'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 11):
    make = 'audi'
    model = 'q7'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 12):
    make = 'ford'
    model = 'f-250'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 13):
    make = 'chevrolet'
    model = 'colorado'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 14):
    make = 'toyota'
    model = 'tundra'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 15):
    make = 'ford'
    model = 'edge'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 16):
    make = 'toyota'
    model = 'land-cruiser'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 17):
    make = 'chevrolet'
    model = 'malibu'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 18):
    make = 'dodge'
    model = 'journey'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 19):
    make = 'lexus'
    model = 'ls'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 20):
    make = 'infiniti'
    model = 'qx50'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 21):
    make = 'mini'
    model = 'hardtop'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 22):
    make = 'lincoln'
    model = 'aviator'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 23):
    make = 'bmw'
    model = '5-series'
elif (datetime.datetime.now().weekday() == 2) & (datetime.datetime.now().hour == 0):
    make = 'mercedes-benz'
    model = 'e-class'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 1):
    make = 'nissan'
    model = 'murano'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 2):
    make = 'mitsubishi'
    model = 'outlander-sport'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 3):
    make = 'nissan'
    model = 'frontier'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 4):
    make = 'subaru'
    model = 'impreza'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 5):
    make = 'acura'
    model = 'ilx'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 6):
    make = 'mazda'
    model = 'cx-9'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 7):
    make = 'ram'
    model = '3500'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 8):
    make = 'hyundai'
    model = 'elantra'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 9):
    make = 'kia'
    model = 'sedona'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 10):
    make = 'buick'
    model = 'encore-gx'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 11):
    make = 'audi'
    model = 'q3'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 12):
    make = 'ford'
    model = 'fusion'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 13):
    make = 'chevrolet'
    model = 'traverse'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 14):
    make = 'toyota'
    model = 'sienna'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 15):
    make = 'honda'
    model = 'pilot'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 16):
    make = 'honda'
    model = 'odyssey'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 17):
    make = 'volkswagen'
    model = 'taos'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 18):
    make = 'dodge'
    model = 'challenger'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 19):
    make = 'lexus'
    model = 'lx'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 20):
    make = 'infiniti'
    model = 'qx80'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 21):
    make = 'mini'
    model = 'countryman'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 22):
    make = 'lincoln'
    model = 'mkz'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 23):
    make = 'bmw'
    model = 'x3'
elif (datetime.datetime.now().weekday() == 3) & (datetime.datetime.now().hour == 0):
    make = 'mercedes-benz'
    model = 'glc'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 1):
    make = 'nissan'
    model = 'titan'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 2):
    make = 'mitsubishi'
    model = 'eclipse-cross'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 3):
    make = 'nissan'
    model = 'versa'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 4):
    make = 'subaru'
    model = 'forester'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 5):
    make = 'acura'
    model = 'tlx'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 6):
    make = 'mazda'
    model = 'mazda3'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 7):
    make = 'ford'
    model = 'expedition'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 8):
    make = 'hyundai'
    model = 'accent'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 9):
    make = 'honda'
    model = 'ridgeline'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 10):
    make = 'buick'
    model = 'century'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 11):
    make = 'audi'
    model = 'a6'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 12):
    make = 'chevrolet'
    model = 'cruze'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 13):
    make = 'chevrolet'
    model = 'camaro'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 14):
    make = 'volkswagen'
    model = 'passat'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 15):
    make = 'gmc'
    model = 'canyon'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 16):
    make = 'jeep'
    model = 'renegade'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 17):
    make = 'jeep'
    model = 'gladiator'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 18):
    make = 'chrysler'
    model = 'town-country'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 19):
    make = 'lexus'
    model = 'es'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 20):
    make = 'infiniti'
    model = 'qx60'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 21):
    make = 'mini'
    model = 'convertible'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 22):
    make = 'lincoln'
    model = 'nautilus'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 23):
    make = 'bmw'
    model = 'x5'
elif (datetime.datetime.now().weekday() == 4) & (datetime.datetime.now().hour == 0):
    make = 'mercedes-benz'
    model = 'gle'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 1):
    make = 'honda'
    model = 'passport'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 2):
    make = 'subaru'
    model = 'legacy'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 3):
    make = 'nissan'
    model = 'armada'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 4):
    make = 'subaru'
    model = 'ascent'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 5):
    make = 'acura'
    model = 'tsx'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 6):
    make = 'mazda'
    model = 'mazda6'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 7):
    make = 'ford'
    model = 'focus'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 8):
    make = 'hyundai'
    model = 'genesis'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 9):
    make = 'kia'
    model = 'telluride'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 10):
    make = 'buick'
    model = 'encore-gx'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 11):
    make = 'audi'
    model = 'a3'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 12):
    make = 'ford'
    model = 'fiesta'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 13):
    make = 'chevrolet'
    model = 'sonic'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 14):
    make = 'toyota'
    model = 'yaris'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 15):
    make = 'honda'
    model = 'fit'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 16):
    make = 'jeep'
    model = 'patriot'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 17):
    make = 'volkswagen'
    model = 'beetle'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 18):
    make = 'dodge'
    model = 'dart'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 19):
    make = 'lexus'
    model = 'rx'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 20):
    make = 'infiniti'
    model = 'q60'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 21):
    make = 'chevrolet'
    model = 'spark'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 22):
    make = 'lincoln'
    model = 'towncar'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 23):
    make = 'bmw'
    model = 'x6'
elif (datetime.datetime.now().weekday() == 5) & (datetime.datetime.now().hour == 0):
    make = 'mercedes-benz'
    model = 'gla'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 1):
    make = 'chevrolet'
    model = 'corvette'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 2):
    make = 'ford'
    model = 'excursion'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 3):
    make = 'tesla'
    model = 'model-3'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 4):
    make = 'subaru'
    model = 'wrx'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 5):
    make = 'tesla'
    model = 'model-y'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 6):
    make = 'mazda'
    model = 'mazda5'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 7):
    make = 'tesla'
    model = 'model-s'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 8):
    make = 'nissan'
    model = '370z'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 9):
    make = 'nissan'
    model = 'kicks'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 10):
    make = 'buick'
    model = 'verano'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 11):
    make = 'buick'
    model = 'regal'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 12):
    make = 'ford'
    model = 'ranger'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 13):
    make = 'chevrolet'
    model = 'trax'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 14):
    make = 'ford'
    model = 'maverick'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 15):
    make = 'kia'
    model = 'optima'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 16):
    make = 'nissan'
    model = 'pathfinder'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 17):
    make = 'hyundai'
    model = 'azera'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 18):
    make = 'kia'
    model = 'k5'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 19):
    make = 'chevrolet'
    model = 'trailblazer'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 20):
    make = 'chevrolet'
    model = 'blazer'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 21):
    make = 'volkswagen'
    model = 'new-beetle'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 22):
    make = 'honda'
    model = 'element'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 23):
    make = 'toyota'
    model = 'prius'
elif (datetime.datetime.now().weekday() == 6) & (datetime.datetime.now().hour == 0):
    make = 'honda'
    model = 'crosstour'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 1):
    make = 'honda'
    model = 'cr-z'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 2):
    make = 'dodge'
    model = 'avenger'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 3):
    make = 'nissan'
    model = 'maxima'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 4):
    make = 'ford'
    model = 'ecosport'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 5):
    make = 'toyota'
    model = '4runner'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 6):
    make = 'toyota'
    model = 'sequoia'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 7):
    make = 'porsche'
    model = 'cayenne'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 8):
    make = 'kia'
    model = 'rio'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 9):
    make = 'dodge'
    model = 'magnum'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 10):
    make = 'honda'
    model = 'hr-v'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 11):
    make = 'volvo'
    model = 's90'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 12):
    make = 'volvo'
    model = 'xc90'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 13):
    make = 'volco'
    model = 'xc60'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 14):
    make = 'volvo'
    model = 's60'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 15):
    make = 'mazda'
    model = 'cx-3'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 16):
    make = 'mazda'
    model = 'cx-30'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 17):
    make = 'volkswagen'
    model = 'atlas'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 18):
    make = 'chrysler'
    model = 'aspen'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 19):
    make = 'lexus'
    model = 'nx'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 20):
    make = 'nissan'
    model = '350z'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 21):
    make = 'mitsubishi'
    model = 'lancer'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 22):
    make = 'lincoln'
    model = 'mkc'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 23):
    make = 'lincoln'
    model = 'mkt'
elif (datetime.datetime.now().weekday() == 0) & (datetime.datetime.now().hour == 0):
    make = 'lincoln'
    model = 'mks'
else:
    make = 'porsche'
    model = 'macan'

print(f'{make.title()} {model.title()}')

Chevrolet Colorado
